In [22]:
from nltk.translate.bleu_score import sentence_bleu

In [16]:
import os
import json
from statistics import mean
import pandas as pd

## Calculate the bleu score
- https://www.digitalocean.com/community/tutorials/bleu-score-in-python
- https://towardsdatascience.com/foundations-of-nlp-explained-bleu-score-and-wer-metrics-1a5ba06d812b/

In [ ]:
base_path = "./validation-output/liuhaotian-llava-v1.5-7b/temp-0.2"
file_name = "lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5.json"

file_path = os.path.join(base_path, file_name)
file = open(file_path, mode="r")
validation_results_dict = json.load(file)

In [ ]:
for results in validation_results_dict:
    ground_truth = results["ground_truth"]
    prediction = results["prediction"]
    # print("ground_truth:", ground_truth)
    # print("prediction:", prediction)
    print(float(sentence_bleu(ground_truth.split(), prediction.split(), weights=(0, 0, 0, 1))))
    # break

## BertScore
- https://medium.com/@abonia/bertscore-explained-in-5-minutes-0b98553bfb71

In [24]:
# from transformers import BertTokenizer, BertModel
from bert_score import BERTScorer

/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


In [25]:
candidate = "The patient is status post median sternotomy. The heart is normal in size. The lungs are clear. There is no pleural effusion or pneumothorax."
reference = "Left-sided subclavian port-a-cath continues to have its tip in the distal svc, near the cavoatrial junction. Heart remains enlarged, which may reflect cardiomegaly, although pericardial effusion should also be considered. Mediastinal contours are unchanged. There is persistent minimal blunting the left costophrenic angle, which may represent a tiny effusion or chronic pleural thickening. Streaky linear opacities at the left base may reflect areas of atelectasis or scarring. No focal airspace consolidation is seen to suggest pneumonia. No pneumothorax. No evidence of pulmonary edema. Linear density overlying the left upper quadrant is likely external to the patient, but clinical correlation would be recommended."
scorer = BERTScorer(model_type='bert-base-uncased', lang="en", device="mps")


def cal_bert_score(scorer, y_true, y_pred):
  '''Calculate BERTScore'''
  # print("y_true:", y_true)
  # print("y_pred:", y_pred)
  P, R, F1 = scorer.score(y_pred, y_true)
  
  P_mean = round(P.mean().item(), 4)
  R_mean = round(R.mean().item(), 4)
  F1_mean = round(F1.mean().item(), 4)

  print(f"BERTScore Precision: {P_mean:.4f}, Recall: {R_mean:.4f}, F1: {F1_mean:.4f}")
  return P_mean, R_mean, F1_mean

# cal_bert_score(scorer=scorer, y_true=[reference], y_pred=[candidate])

/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/huggingface_hub/file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/bitsandbytes/cextension.py:34: UserWarning: The installed version of bitsandbytes was compiled without GPU support. 8-bit optimizers, 8-bit multiplication, and GPU quantization are unavailable.
  warn("The installed version of bitsandbytes was compiled without GPU support. "


'NoneType' object has no attribute 'cadam32bit_grad_fp32'


/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


In [26]:
def get_single_model_bert_score(output_path):
  y_true = []
  y_pred = []
  file = open(output_path)
  print("output_path:", output_path)
  results_list_dict = json.load(file)
  for r in results_list_dict:
    y_true.append(r["ground_truth"])
    y_pred.append(r["prediction"])
    # print("ground_truth", ground_truth)
    # print("prediction", prediction)
  
  score = cal_bert_score(scorer, y_true=y_true, y_pred=y_pred)

  return score
  

In [ ]:
# get_single_model_bert_score("./validation-output/train-5k-quantized-4-default.json")

In [27]:
def get_all_bert_scores(base_dir, output_file_path):
    results_dict = {}
  
    for root, _, files in os.walk(base_dir):  # Recursively walk through directories
        for file in files:
            # print("file:", file)
            full_path = os.path.join(root, file)
            if "temp-0.2" in full_path and file.endswith(".json"):
                fileprefix = full_path[:-5]
                filename = fileprefix.split("/")[-1]
                P, R, F1 = get_single_model_bert_score(full_path)
                results_dict[filename] = {"precision":P, "recall": R, "F1": F1}

    with open(output_file_path, "w") as file:
        json.dump(results_dict, file)
    
    return results_dict

## CheXpert F1

### 1a) Gather all ground truths and predictions

In [2]:
import json
import csv
import os


In [3]:
def compile_individual_report(json_file_path, ground_truth_csv, prediction_csv):
  """Extract out the ground truth and the generated output"""
  # Load JSON data
  with open(json_file_path, "r", encoding="utf-8") as file:
      data = json.load(file)

  # Extract ground truths and predictions
  ground_truths = [[entry["ground_truth"]] for entry in data]
  predictions = [[entry["prediction"]] for entry in data]
  
  print("ground_truths:", ground_truths)
  print("predictions:", predictions)


  # Write ground truths to CSV file
  with open(ground_truth_csv, "w", encoding="utf-8", newline='') as file:
      writer = csv.writer(file)
      # writer.writerow(["ground_truth"])
      writer.writerows(ground_truths)

  # Write predictions to CSV file
  with open(prediction_csv, "w", encoding="utf-8", newline='') as file:
      writer = csv.writer(file)
      # writer.writerow(["prediction"])
      writer.writerows(predictions)

  print("Extraction complete. Ground truths and predictions saved as CSV files.")

In [4]:
# compile_individual_report(
#   "./validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-layers-2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5.json",
#   "./validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-layers-2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5-ground-truth.csv",
#   "./validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-layers-2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5-prediction.csv"
#   )

In [5]:
# compile_individual_report(
#   "./validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/liuhaotian-llava-v1.5-7b.json",
#   "./validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/liuhaotian-llava-v1.5-7b-ground-truth.csv",
#   "./validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/liuhaotian-llava-v1.5-7b-prediction.csv"
#   )

In [6]:
def compile_reports(base_dir):
    """Compile all the ground truth and the generated output"""
    for root, _, files in os.walk(base_dir):  # Recursively walk through directories
        for file in files:
            # print("file:", file)
            full_path = os.path.join(root, file)
            if "temp-0.2" in full_path and file.endswith(".json"):
                fileprefix = full_path[:-5]
                # print("full_path:", full_path)
                print("fileprefix:", fileprefix)

                # ground_truth_path = fileprefix+"-ground-truth.csv"
                # prediction_path = fileprefix+"-prediction.csv"
                # print("ground_truth_path:", ground_truth_path)
                # print("prediction_path:", prediction_path)

                compile_individual_report(full_path, fileprefix+"-ground-truth.csv", fileprefix+"-prediction.csv")

fileprefix: ./validation-output/microsoft-llava-med-v1.5-mistral-7b/temp-0.2/lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-3-lr-6e-5
ground_truths: [['Left-sided subclavian port-a-cath continues to have its tip in the distal svc, near the cavoatrial junction. Heart remains enlarged, which may reflect cardiomegaly, although pericardial effusion should also be considered. Mediastinal contours are unchanged. There is persistent minimal blunting the left costophrenic angle, which may represent a tiny effusion or chronic pleural thickening. Streaky linear opacities at the left base may reflect areas of atelectasis or scarring. No focal airspace consolidation is seen to suggest pneumonia. No pneumothorax. No evidence of pulmonary edema. Linear density overlying the left upper quadrant is likely external to the patient, but clinical correlation would be recommended.'], ['New right ij central venous line with tip likely within the right atrium an

### 1b) Calculate the precision, recall and F1 score for each model

Do this by comparing the ground truth and predicited output's class labels for the 14 different diseases

In [17]:
import pandas as pd
from sklearn.metrics import f1_score, recall_score, precision_score

In [36]:
def fill_default(filepath, output_file_path=None):
  """Replace the NaN columns with a default value of 2. These pathologies are not mentioned in the report"""
  df = pd.read_csv(filepath)
  df.fillna(2.0, inplace=True)

  if output_file_path==None:
    df.to_csv(f"{filepath}", index=False, mode="w")
  else:
    df.to_csv(f"{output_file_path}", index=False, mode="w")

# fill_default("./chexpert/liuhaotian-llava-v1.5-7b-ground-truth.csv")
# fill_default("./chexpert/liuhaotian-llava-v1.5-7b-prediction.csv")

In [66]:
def add_study_id(json_path, csv_path):
  """add the study to the chexpert output"""
  json_df = pd.read_json(json_path)
  csv_df = pd.read_csv(csv_path)
  assert len(json_df) == len(csv_df)

  if "study_id" in csv_df:
    return

  study_ids = list(json_df["study_id"])
  # print(study_ids)

  csv_df.insert(0, "study_id", study_ids)
  csv_df.to_csv(csv_path, index=False, mode="w")



def preprocess(base_dir, chexpert_dir):
    """
    Preprocesses all the outputs from chexpert labeller:
    1) Replce all NaN with default value of 2
    2) Add study id
    """
    for root, _, files in os.walk(base_dir):  # Recursively walk through directories
        for file in files:
            # if file == "liuhaotian-llava-v1.5-7b.json":
            #     continue
            # print("file:", file)
            full_path = os.path.join(root, file)
            if "temp-0.2" in full_path and file.endswith(".json"):
                fileprefix = full_path[:-5]
                filename = fileprefix.split("/")[-1]

                ground_truth_path = os.path.join(chexpert_dir, filename+"-ground-truth.csv")
                prediction_path = os.path.join(chexpert_dir, filename+"-prediction.csv")
                # replace NaN with default value of 2
                fill_default(prediction_path)
                fill_default(ground_truth_path)

                # add study id
                add_study_id(full_path, ground_truth_path)
                add_study_id(full_path, prediction_path)


# add_study_id(
#   "validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/liuhaotian-llava-v1.5-7b.json", 
#   "chexpert/validation/liuhaotian-llava-v1.5-7b-ground-truth.csv"
#   )

# add_study_id(
#   "validation-output/liuhaotian-llava-v1.5-7b/temp-0.2/liuhaotian-llava-v1.5-7b.json", 
#   "chexpert/validation/liuhaotian-llava-v1.5-7b-prediction.csv"
#   )

In [68]:
def get_individual_chexpert_validate_results(ground_truth_path, prediction_path, average="micro"):
  ground_truth_df = pd.read_csv(ground_truth_path)
  prediction_df = pd.read_csv(prediction_path)
  assert len(ground_truth_df) == len(prediction_df)

  rows = len(ground_truth_df)
  recall_scores = []
  precision_scores = []
  f1_scores = []
  for i in range(0, rows-1):
    prediction_classification = prediction_df.iloc[i, 2:].tolist()
    ground_truth_classification = ground_truth_df.iloc[i, 2:].tolist()
    # print("len(ground_truth_classification):", len(ground_truth_classification))
    # print("len(prediction_classification):", len(prediction_classification))

    # iterate through each of the class labels
    # pop indices whereby the ground truth == 2 (cannot determine whether the generated output is correct or wrong)
    # but if the ground truth != 2 and the generated output == 2, it can be taken as a wrong classification 
    # since the generated output does not contain information about that pathology

    # 14 pathologies
    for index in range(13, -1, -1):
      # start from the back as we want to pop elements from the list
      if int(ground_truth_classification[index]) == 2:
        # print("index:", index, "ground_truth_classification[index]:", ground_truth_classification[index])
        ground_truth_classification.pop(index)
        prediction_classification.pop(index)


    recall = recall_score(ground_truth_classification, prediction_classification, average=average)
    prec = precision_score(ground_truth_classification, prediction_classification, average=average)
    f1 = f1_score(ground_truth_classification, prediction_classification, average=average)

    recall_scores.append(recall)
    precision_scores.append(prec)
    f1_scores.append(f1)

  return round(mean(recall_scores), 4), round(mean(precision_scores), 4), round(mean(f1_scores), 4)

recall, precision, f1 = get_individual_chexpert_validate_results(
  "chexpert/validation/liuhaotian-llava-v1.5-7b-ground-truth.csv",
  "chexpert/validation/liuhaotian-llava-v1.5-7b-prediction.csv"
  )
print(recall, precision, f1)

0.0882 0.0882 0.0882


In [69]:
def get_chexpert_validate_results(base_dir, chexpert_dir, output_file_path):
    results_dict = {}
    for root, _, files in os.walk(base_dir):  # Recursively walk through directories
        for file in files:
            # if file == "liuhaotian-llava-v1.5-7b.json":
            #     continue
            # print("file:", file)
            full_path = os.path.join(root, file)
            if "temp-0.2" in full_path and file.endswith(".json"):
                fileprefix = full_path[:-5]
                filename = fileprefix.split("/")[-1]

                ground_truth_path = os.path.join(chexpert_dir, filename+"-ground-truth.csv")
                prediction_path = os.path.join(chexpert_dir, filename+"-prediction.csv")
                # replace NaN with default value of 2
                fill_default(prediction_path)
                fill_default(ground_truth_path)

                # add study id
                add_study_id(full_path, ground_truth_path)
                add_study_id(full_path, prediction_path)

                recall, precision, f1 = get_individual_chexpert_validate_results(ground_truth_path, prediction_path, average="micro")

                results_dict[filename] = {"precision":precision, "recall": recall, "F1": f1}

    with open(output_file_path, "w") as file:
        json.dump(results_dict, file)
    
    return results_dict


## Validation Results

In [33]:
get_all_bert_scores("./validation-output", "./results/validation-bertscore.json")

output_path: ./validation-output/microsoft-llava-med-v1.5-mistral-7b/temp-0.2/lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-3-lr-6e-5.json
BERTScore Precision: 0.6969, Recall: 0.6256, F1: 0.6576
output_path: ./validation-output/microsoft-llava-med-v1.5-mistral-7b/temp-0.2/lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5.json
BERTScore Precision: 0.6991, Recall: 0.6221, F1: 0.6568
output_path: ./validation-output/microsoft-llava-med-v1.5-mistral-7b/temp-0.2/microsoft-llava-med-v1.5-mistral-7b.json
BERTScore Precision: 0.5208, Recall: 0.5145, F1: 0.5168
output_path: ./validation-output/microsoft-llava-med-v1.5-mistral-7b/temp-0.2/lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5.json
BERTScore Precision: 0.6886, Recall: 0.6176, F1: 0.6497
output_path: ./validation-output/llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2/tem

{'lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-3-lr-6e-5': {'precision': 0.6969,
  'recall': 0.6256,
  'F1': 0.6576},
 'lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5': {'precision': 0.6991,
  'recall': 0.6221,
  'F1': 0.6568},
 'microsoft-llava-med-v1.5-mistral-7b': {'precision': 0.5208,
  'recall': 0.5145,
  'F1': 0.5168},
 'lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5': {'precision': 0.6886,
  'recall': 0.6176,
  'F1': 0.6497},
 'llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2': {'precision': 0.4727,
  'recall': 0.4519,
  'F1': 0.4615},
 'lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5': {'precision': 0.6877,
  'recall': 0.5786,
  'F1': 0.6272},
 'lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-tr

In [31]:
compile_reports("./validation-output")

fileprefix: ./validation-output/microsoft-llava-med-v1.5-mistral-7b/temp-0.2/lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-3-lr-6e-5
ground_truths: [['Left-sided subclavian port-a-cath continues to have its tip in the distal svc, near the cavoatrial junction. Heart remains enlarged, which may reflect cardiomegaly, although pericardial effusion should also be considered. Mediastinal contours are unchanged. There is persistent minimal blunting the left costophrenic angle, which may represent a tiny effusion or chronic pleural thickening. Streaky linear opacities at the left base may reflect areas of atelectasis or scarring. No focal airspace consolidation is seen to suggest pneumonia. No pneumothorax. No evidence of pulmonary edema. Linear density overlying the left upper quadrant is likely external to the patient, but clinical correlation would be recommended.'], ['New right ij central venous line with tip likely within the right atrium an

In [70]:
preprocess("./validation-output", "./chexpert/validation")

In [71]:
chexpert_results = get_chexpert_validate_results("./validation-output", "./chexpert/validation", "./results/validation-chexpert.json")

In [75]:
chexpert_df = pd.read_json("results/validation-chexpert.json")
chexpert_df.rename({"precision": "chexpert_precision", "recall": "chexpert_recall", "F1": "chexpert_f1"}, inplace=True)
# chexpert_df

In [76]:
bert_df = pd.read_json("results/validation-bertscore.json")
bert_df.rename({"precision": "bert_precision", "recall": "bert_recall", "F1": "bert_f1"}, inplace=True)
# bert_df

In [80]:
pd.concat([chexpert_df, bert_df]).loc[["chexpert_f1", "bert_f1"]]

lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-3-lr-6e-5  \
chexpert_f1                                             0.3440                                                         
bert_f1                                                 0.6576                                                         

             lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5  \
chexpert_f1                                             0.3174                                                         
bert_f1                                                 0.6568                                                         

             microsoft-llava-med-v1.5-mistral-7b  \
chexpert_f1                               0.1615   
bert_f1                                   0.5168   

             lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5  \
chexpert_f1                                             0.3065                                                         
bert_f1                                                 0.6497                                                         

             llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2  \
chexpert_f1                                             0.0448             
bert_f1                                                 0.4615             

             lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5  \
chexpert_f1                                             0.1695                                                                                 
bert_f1                                                 0.6272                                                                                 

             lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5-cls-patch  \
chexpert_f1                                             0.1731                                                                                           
bert_f1                                                 0.6270                                                                                           

             lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5  \
chexpert_f1                                             0.1661                                                                                 
bert_f1                                                 0.5194                                                                                 

             lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-unquantized-epoch-1-lr-6e-5-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5  \
chexpert_f1                                             0.1347                                                                                                                                        
bert_f1                                                 0.6193                                                                                                                                        

             lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5  \
chexpert_f1                                             0.3991                                                                             
bert_f1                                                 0.6623                                                                             

             liuhaotian-llava-v1.5-7b  \
chexpert_f1                    0.0882   
bert_f1                        0.4946   

             lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.000

## Test results

In [132]:
get_all_bert_scores("./test-output", "./results/test-bertscore.json")

output_path: ./test-output/temp-0.2/lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5.json
BERTScore Precision: 0.6860, Recall: 0.6281, F1: 0.6534
output_path: ./test-output/temp-0.2/lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-3-lr-6e-5.json
BERTScore Precision: 0.6914, Recall: 0.6155, F1: 0.6493
output_path: ./test-output/temp-0.2/liuhaotian-llava-v1.5-7b.json
BERTScore Precision: 0.4841, Recall: 0.4639, F1: 0.4730
output_path: ./test-output/temp-0.2/lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5.json
BERTScore Precision: 0.6899, Recall: 0.6103, F1: 0.6457
output_path: ./test-output/temp-0.2/lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5.json
BERTScore Precision: 0.6689, Recall: 0.5665, F1: 0.6120
output_path: ./test-output/tem

{'lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5': {'precision': 0.686,
  'recall': 0.6281,
  'F1': 0.6534},
 'lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-3-lr-6e-5': {'precision': 0.6914,
  'recall': 0.6155,
  'F1': 0.6493},
 'liuhaotian-llava-v1.5-7b': {'precision': 0.4841,
  'recall': 0.4639,
  'F1': 0.473},
 'lora-microsoft-llava-med-v1.5-mistral-7b-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5': {'precision': 0.6899,
  'recall': 0.6103,
  'F1': 0.6457},
 'lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5': {'precision': 0.6689,
  'recall': 0.5665,
  'F1': 0.612},
 'llava-med-v1.5-mistral-7b': {'precision': 0.5235,
  'recall': 0.5151,
  'F1': 0.5183},
 'lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-train_28k_custom-train-mlp-and-llm-unquantized-epoc

In [37]:
# fill_default("./raw_data/mimic-cxr-2.1.0-test-set-labeled.csv", "./processed_data/mimic-cxr-2.1.0-test-set-labeled.csv")

In [129]:
compile_reports("./test-output")

fileprefix: ./test-output/temp-0.2/lora-liuhaotian-llava-v1.5-7b-vision_tower-epoch-1-lr-0.0001-train_28k_custom-train-mlp-and-llm-unquantized-epoch-2-lr-6e-5
ground_truths: [['Frontal view of the chest was obtained. A right subclavian central catheter terminates in the lower svc. Metallic clips overlie the right upper quadrant. The heart is of normal size with normal cardiomediastinal contours. Vague bibasilar opacities are nonspecific but may represent infection. No pleural effusion or pneumothorax.'], ['Ap portable upright view of the chest. Evaluation limited due to underpenetration and low lung volumes. There is cardiomegaly with hilar congestion and mild pulmonary edema. No large effusion is seen the small effusions difficult to exclude. No overt signs of pneumonia though lung bases are suboptimally assessed. No large pneumothorax.'], ['Pacemaker leads terminate in right atrium and ventricle. Right picc line tip is at the level of mid svc. Heart size and mediastinum are unchanged

In [122]:
# def get_individual_chexpert_test_results(ground_truth_path, prediction_path, average="micro"):
#   ground_truth_df = pd.read_csv(ground_truth_path)
#   prediction_df = pd.read_csv(prediction_path)
#   # assert len(ground_truth_df) == len(prediction_df)

#   rows = len(ground_truth_df)
#   recall_scores = []
#   precision_scores = []
#   f1_scores = []
#   for i in range(0, rows-1):
#     study_id = prediction_df.iloc[i]["study_id"]
#     print("study_id:", study_id)
#     ground_truth_row = ground_truth_df.loc[ground_truth_df['study_id'] == study_id]
#     print("ground_truth_row:", ground_truth_row)
#     ground_truth_classification = ground_truth_row.iloc[:, 1:].values
#     # .flatten().tolist()
#     print("ground_truth_classification:", ground_truth_classification)

#     prediction_classification = prediction_df.iloc[i, 2:].tolist()

#     # print("prediction_classification:", len(prediction_classification))
#     # print("ground_truth_classification:", len(ground_truth_classification))
#     assert len(prediction_classification) == len(ground_truth_classification)

#     # iterate through each of the class labels
#     # pop indices whereby the ground truth == 2 (cannot determine whether the generated output is correct or wrong)
#     # but if the ground truth != 2 and the generated output == 2, it can be taken as a wrong classification 
#     # since the generated output does not contain information about that pathology

#     # 14 pathologies
#     for index in range(13, -1, -1):
#       # start from the back as we want to pop elements from the list
#       if int(ground_truth_classification[index]) == 2:
#         # print("index:", index, "ground_truth_classification[index]:", ground_truth_classification[index])
#         ground_truth_classification.pop(index)
#         prediction_classification.pop(index)


#     recall = recall_score(ground_truth_classification, prediction_classification, average=average)
#     prec = precision_score(ground_truth_classification, prediction_classification, average=average)
#     f1 = f1_score(ground_truth_classification, prediction_classification, average=average)

#     recall_scores.append(recall)
#     precision_scores.append(prec)
#     f1_scores.append(f1)

#   return round(mean(recall_scores), 4), round(mean(precision_scores), 4), round(mean(f1_scores), 4)


# recall, precision, f1 = 
# get_individual_chexpert_test_results(
#   "processed_data/mimic-cxr-2.1.0-test-set-labeled.csv",
#   "chexpert/test/lora-llava-med-v1.5-mistral-7b-vision_tower-epoch-1-lr-0.0001-v2-train_28k_custom-train-mlp-and-llm-unquantized-epoch-1-lr-6e-5-ground-truth.csv",
#   )
# print(recall, precision, f1)


# def get_chexpert_test_results(base_dir, chexpert_dir, output_file_path, ground_truth_path="chexpert/validation/liuhaotian-llava-v1.5-7b-ground-truth.csv"):
#     results_dict = {}
#     for root, _, files in os.walk(base_dir):  # Recursively walk through directories
#         for file in files:
#             # if file == "liuhaotian-llava-v1.5-7b.json":
#             #     continue
#             # print("file:", file)
#             full_path = os.path.join(root, file)
#             if "temp-0.2" in full_path and file.endswith(".json"):
#                 fileprefix = full_path[:-5]
#                 filename = fileprefix.split("/")[-1]

#                 prediction_path = os.path.join(chexpert_dir, filename+"-prediction.csv")
#                 fill_default(prediction_path)

#                 recall, precision, f1 = get_individual_chexpert_validate_results(ground_truth_path, prediction_path, average="micro")

#                 results_dict[filename] = {"precision":precision, "recall": recall, "F1": f1}

#     with open(output_file_path, "w") as file:
#         json.dump(results_dict, file)
    
#     return results_dict


In [130]:
preprocess("./test-output", "./chexpert/test")

In [131]:
chexpert_results = get_chexpert_validate_results("./test-output", "./chexpert/test", "./results/test-chexpert.json")

/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/kaijun/opt/anaconda3/envs/llava-med/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1609: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, "true nor predicted", "F-score is", len(true_sum))
/Users/kaijun/o